In [1]:
import time

import numpy as np
import pandas as pd
import torch
from torch import nn
from tqdm import tqdm

# random seed
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed(42)

In [2]:
# turn off warning
import logging
logging.getLogger('pyomo.core').setLevel(logging.ERROR)

## Problem Setting

In [3]:
# init
num_var = 50      # number of variables
num_ineq = 50     # number of constraints
num_data = 10000  # number of data
test_size = 1000  # number of test size
val_size = 1000   # number of validation size
train_size = num_data - test_size - val_size

In [4]:
# data sample from uniform distribution
b_samples = torch.from_numpy(np.random.uniform(-1, 1, size=(num_data, num_ineq))).float()
data = {"b":b_samples}
# data split
from src.utlis import data_split
data_train, data_test, data_dev = data_split(data, test_size=test_size, val_size=val_size)

In [5]:
# torch dataloaders
from torch.utils.data import DataLoader
batch_size = 64
loader_train = DataLoader(data_train, batch_size, num_workers=0, collate_fn=data_train.collate_fn, shuffle=True)
loader_test = DataLoader(data_test, batch_size, num_workers=0, collate_fn=data_test.collate_fn, shuffle=False)
loader_dev = DataLoader(data_dev, batch_size, num_workers=0, collate_fn=data_dev.collate_fn, shuffle=False)

## Exact Solver

In [6]:
from src.problem import msNonconvex
model = msNonconvex(num_var, num_ineq, timelimit=60)

In [7]:
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"][:100]):
    # set params
    model.set_param_val({"b":b.cpu().numpy()})
    # solve
    tick = time.time()
    try:
        xval, objval = model.solve("scip")
        # eval
        params.append(list(b))
        sols.append(list(list(xval.values())[0].values()))
        objvals.append(objval)
        conviols.append(sum(model.cal_violation()))
    except:
        params.append(list(b))
        sols.append(None)
        objvals.append(None)
        conviols.append(None)
    tock = time.time()
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
print("Number of None values: ", df["Sol"].isna().sum())
df.to_csv("result/nc_exact_50-50.csv")

  0%|                                                                                          | 0/100 [00:00<?, ?it/s]

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

  2%|█▌                                                                              | 2/100 [01:11<1:05:14, 39.95s/it]

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

  3%|██▍                                                                               | 3/100 [01:13<36:15, 22.43s/it]

...

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

 99%|████████████████████████████████████████████████████████████████████████████████▏| 99/100 [32:28<00:41, 41.03s/it]

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [32:31<00:00, 19.51s/it]


         Obj Val  Constraints Viol  Elapsed Time
count  23.000000         23.000000    100.000000
mean   18.874385          1.669633     19.512184
std    17.718651          2.059988     24.276865
min     1.060347          0.000000      1.131553
25%     7.093541          0.000000      2.200904
50%    11.729067          0.000000      5.881238
75%    26.515944          3.547399     44.460227
max    81.611728          5.407014     62.740271
Number of infeasible solution: 11
Number of None values:  77


In [8]:
df = pd.read_csv("result/nc_exact_50-50.csv", index_col=0).iloc[:100]
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
print("Number of None values: ", df["Sol"].isna().sum())

         Obj Val  Constraints Viol  Elapsed Time
count  23.000000         23.000000    100.000000
mean   18.874385          1.669633     19.512184
std    17.718651          2.059988     24.276865
min     1.060347          0.000000      1.131553
25%     7.093541          0.000000      2.200904
50%    11.729067          0.000000      5.881238
75%    26.515944          3.547399     44.460227
max    81.611728          5.407014     62.740271
Number of infeasible solution: 11
Number of None values:  77


## Heuristic - Round

In [10]:
from src.heuristic import naive_round

In [11]:
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"][:100]):
    # set params
    model.set_param_val({"b":b.cpu().numpy()})
    # relax
    model_rel = model.relax()
    # solve
    tick = time.time()
    xval_rel, _ = model_rel.solve("scip")
    xval, objval = naive_round(xval_rel, model)
    tock = time.time()
    # eval
    params.append(list(b))
    sols.append(list(list(xval.values())[0].values()))
    objvals.append(objval)
    conviols.append(sum(model.cal_violation()))
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
df.to_csv("result/nc_heur_rnd_50-50.csv")

100%|██████████████████████████████████████████████████████████████████████████████| 100/100 [1:30:55<00:00, 54.56s/it]


          Obj Val  Constraints Viol  Elapsed Time
count  100.000000        100.000000    100.000000
mean    -0.782491          2.719736     54.475435
std      0.639810          2.842095     13.671189
min     -1.918758          0.026950      9.098947
25%     -1.258223          0.833649     59.632188
50%     -0.710524          1.413203     60.198215
75%     -0.264735          4.015034     60.272435
max      0.752153         10.775361     61.185207
Number of infeasible solution: 100


## Heuristic - N1

In [7]:
model_heur = model.first_solution_heuristic(nodes_limit=1)

In [8]:
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"]):
    # set params
    model_heur.set_param_val({"b":b.cpu().numpy()})
    # solve
    tick = time.time()
    try:
        xval, objval = model_heur.solve("scip")
        # eval
        params.append(list(b))
        sols.append(list(list(xval.values())[0].values()))
        objvals.append(objval)
        conviols.append(sum(model_heur.cal_violation()))
    except:
        params.append(list(b))
        sols.append(None)
        objvals.append(None)
        conviols.append(None)
    tock = time.time()
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
print("Number of None values: ", df["Sol"].isna().sum())
df.to_csv("result/nc_heur_n1_50-50.csv")

  0%|                                                                                         | 0/1000 [00:00<?, ?it/s]

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

  0%|▏                                                                              | 3/1000 [00:48<3:56:20, 14.22s/it]

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

  0%|▎                                                                              | 4/1000 [00:49<2:31:42,  9.14s/it]

...

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

100%|████████████████████████████████████████████████████████████████████████████▉| 999/1000 [4:02:05<00:22, 22.19s/it]

ERROR: Solver (scip) returned non-zero return code (4294967295)
ERROR: Solver log: WARNING: unknown parameter <quiet> SCIP version 8.1.0
[precision: 8 byte] [memory: block] [mode: optimized] [LP solver: Soplex
6.0.4] [GitHash: 6129793871] Copyright (c) 2002-2023 Zuse Institute Berlin
(ZIB)

    External libraries:
      Soplex 6.0.4         Linear Programming Solver developed at Zuse
      Institute Berlin (soplex.zib.de) [GitHash: 950b1658] CppAD 20180000.0
      Algorithmic Differentiation of C++ algorithms developed by B. Bell
      (github.com/coin-or/CppAD) ZLIB 1.2.13          General purpose
      compression library by J. Gailly and M. Adler (zlib.net) AMPL/MP
      4e2d45c4     AMPL .nl file reader library (github.com/ampl/mp) PaPILO
      2.1.4         parallel presolve for integer and linear optimization
      (github.com/scipopt/papilo) [GitHash: ee0677c4] bliss 0.77
      Computing Graph Automorphism Groups by T. Junttila and P. Kaski
      (https://users.aalto.fi/~tjuntti

100%|████████████████████████████████████████████████████████████████████████████| 1000/1000 [4:02:07<00:00, 14.53s/it]


            Obj Val  Constraints Viol  Elapsed Time
count  4.460000e+02        446.000000   1000.000000
mean   8.720169e+05          0.729643     14.525758
std    1.597607e+07          1.536783     68.897491
min   -3.187476e-02          0.000000      0.687065
25%    1.514668e+01          0.000000      1.751524
50%    2.834759e+01          0.000000      4.077335
75%    9.449784e+01          0.000000     13.301839
max    3.365937e+08          7.753283   2114.064270
Number of infeasible solution: 100
Number of None values:  554


In [12]:
df = pd.read_csv("result/nc_heur_n1_50-50.csv", index_col=0).iloc[:100]
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
print("Number of None values: ", df["Sol"].isna().sum())

           Obj Val  Constraints Viol  Elapsed Time
count    43.000000         43.000000    100.000000
mean    289.992327          0.908906     11.449741
std    1008.712044          1.697968     18.647171
min       5.689244          0.000000      0.706179
25%      11.729067          0.000000      1.352410
50%      17.727392          0.000000      3.199822
75%      37.323113          0.718886      9.935531
max    6171.800840          5.384386     61.004951
Number of infeasible solution: 11
Number of None values:  57


## Learnable Rounding

In [13]:
# random seed
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed(42)

In [14]:
# hyperparameters
penalty_weight = 100  # weight of constraint violation penealty
hlayers_sol = 5       # number of hidden layers for solution mapping
hlayers_rnd = 4       # number of hidden layers for solution mapping
hsize = 128           # width of hidden layers for solution mapping
lr = 1e-3             # learning rate

In [15]:
# set problem
import neuromancer as nm
from src.problem import nmNonconvex
from src.func.layer import netFC
from src.func import roundGumbelModel
# build neural architecture for the solution map
func = nm.modules.blocks.MLP(insize=num_ineq, outsize=num_var, bias=True,
                             linear_map=nm.slim.maps["linear"],
                             nonlin=nn.ReLU, hsizes=[hsize]*hlayers_sol)
smap = nm.system.Node(func, ["b"], ["x"], name="smap")
# define rounding model
layers_rnd = netFC(input_dim=num_ineq+num_var, hidden_dims=[hsize]*hlayers_rnd, output_dim=num_var)
rnd = roundGumbelModel(layers=layers_rnd, param_keys=["b"], var_keys=["x"],  output_keys=["x_rnd"], 
                       int_ind=model.int_ind, continuous_update=True, name="round")
# build neuromancer problem for rounding
components = nn.ModuleList([smap, rnd]).to("cuda")
loss_fn = nmNonconvex(["b", "x_rnd"], num_var, num_ineq, penalty_weight)

In [16]:
from src.problem.neuromancer.trainer import trainer
# training
epochs = 200                    # number of training epochs
warmup = 20                     # number of epochs to wait before enacting early stopping policy
patience = 20                   # number of epochs with no improvement in eval metric to allow before early stopping
optimizer = torch.optim.AdamW(components.parameters(), lr=lr)
# create a trainer for the problem
my_trainer = trainer(components, loss_fn, optimizer, epochs, patience, warmup, device="cuda")
# training for the rounding problem
my_trainer.train(loader_train, loader_dev)

Epoch 0, Validation Loss: 1485.64
Epoch 1, Validation Loss: 4.42
Epoch 2, Validation Loss: 3.18
Epoch 3, Validation Loss: 2.52
Epoch 4, Validation Loss: 2.34
Epoch 5, Validation Loss: 2.37
Epoch 6, Validation Loss: 2.13
Epoch 7, Validation Loss: 2.05
Epoch 8, Validation Loss: 2.20
Epoch 9, Validation Loss: 2.46
Epoch 10, Validation Loss: 2.04
Epoch 11, Validation Loss: 2.02
Epoch 12, Validation Loss: 1.98
Epoch 13, Validation Loss: 1.89
Epoch 14, Validation Loss: 1.87
Epoch 15, Validation Loss: 1.97
Epoch 16, Validation Loss: 1.72
Epoch 17, Validation Loss: 1.78
Epoch 18, Validation Loss: 1.69
Epoch 19, Validation Loss: 1.49
Epoch 20, Validation Loss: 1.70
Epoch 21, Validation Loss: 1.80
Epoch 22, Validation Loss: 1.37
Epoch 23, Validation Loss: 1.43
Epoch 24, Validation Loss: 1.33
Epoch 25, Validation Loss: 1.86
Epoch 26, Validation Loss: 1.29
Epoch 27, Validation Loss: 1.48
Epoch 28, Validation Loss: 1.31
Epoch 29, Validation Loss: 1.29
Epoch 30, Validation Loss: 1.27
Epoch 31, Valid

In [17]:
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"][:100]):
    # data point as tensor
    datapoints = {"b": torch.unsqueeze(b, 0).to("cuda"), 
                  "name": "test"}
    # infer
    components.eval()
    tick = time.time()
    with torch.no_grad():
        for comp in components:
            datapoints.update(comp(datapoints))
    tock = time.time()
    # assign params
    model.set_param_val({"b":b.cpu().numpy()})
    # assign vars
    x = datapoints["x_rnd"]
    for i in range(num_var):
        model.vars["x"][i].value = x[0,i].item()
    # get solutions
    xval, objval = model.get_val()    
    params.append(list(b.cpu().numpy()))
    sols.append(list(list(xval.values())[0].values()))
    objvals.append(objval)
    conviols.append(sum(model.cal_violation()))
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
df.to_csv("result/nc_lr_50-50.csv")

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [00:01<00:00, 82.76it/s]


          Obj Val  Constraints Viol  Elapsed Time
count  100.000000        100.000000    100.000000
mean     0.677968          0.000114      0.002549
std      0.104277          0.000807      0.000553
min      0.518181          0.000000      0.001503
25%      0.597104          0.000000      0.002000
50%      0.648854          0.000000      0.002507
75%      0.742393          0.000000      0.003002
max      0.995029          0.006249      0.003739
Number of infeasible solution: 2


## Learnable Threshold

In [18]:
# random seed
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed(42)

In [19]:
# hyperparameters
penalty_weight = 100  # weight of constraint violation penealty
hlayers_sol = 5       # number of hidden layers for solution mapping
hlayers_rnd = 4       # number of hidden layers for solution mapping
hsize = 128           # width of hidden layers for solution mapping
lr = 1e-3             # learning rate

In [20]:
# set problem
import neuromancer as nm
from src.problem import nmNonconvex
from src.func.layer import netFC
from src.func import roundThresholdModel
# build neural architecture for the solution map
func = nm.modules.blocks.MLP(insize=num_ineq, outsize=num_var, bias=True,
                             linear_map=nm.slim.maps["linear"],
                             nonlin=nn.ReLU, hsizes=[hsize]*hlayers_sol)
smap = nm.system.Node(func, ["b"], ["x"], name="smap")
# define rounding model
layers_rnd = netFC(input_dim=num_ineq+num_var, hidden_dims=[hsize]*hlayers_rnd, output_dim=num_var)
rnd = roundThresholdModel(layers=layers_rnd, param_keys=["b"], var_keys=["x"],  output_keys=["x_rnd"], 
                       int_ind=model.int_ind, continuous_update=True, name="round")
# build neuromancer problem for rounding
components = nn.ModuleList([smap, rnd]).to("cuda")
loss_fn = nmNonconvex(["b", "x_rnd"], num_var, num_ineq, penalty_weight)

In [21]:
from src.problem.neuromancer.trainer import trainer
# training
epochs = 200                    # number of training epochs
warmup = 20                     # number of epochs to wait before enacting early stopping policy
patience = 20                   # number of epochs with no improvement in eval metric to allow before early stopping
optimizer = torch.optim.AdamW(components.parameters(), lr=lr)
# create a trainer for the problem
my_trainer = trainer(components, loss_fn, optimizer, epochs, patience, warmup, device="cuda")
# training for the rounding problem
my_trainer.train(loader_train, loader_dev)

Epoch 0, Validation Loss: 1241.19
Epoch 1, Validation Loss: 2.27
Epoch 2, Validation Loss: 1.60
Epoch 3, Validation Loss: 1.52
Epoch 4, Validation Loss: 2.64
Epoch 5, Validation Loss: 1.24
Epoch 6, Validation Loss: 1.32
Epoch 7, Validation Loss: 1.40
Epoch 8, Validation Loss: 1.49
Epoch 9, Validation Loss: 1.42
Epoch 10, Validation Loss: 1.05
Epoch 11, Validation Loss: 1.08
Epoch 12, Validation Loss: 1.14
Epoch 13, Validation Loss: 0.97
Epoch 14, Validation Loss: 1.26
Epoch 15, Validation Loss: 0.95
Epoch 16, Validation Loss: 1.48
Epoch 17, Validation Loss: 0.80
Epoch 18, Validation Loss: 1.10
Epoch 19, Validation Loss: 0.65
Epoch 20, Validation Loss: 0.80
Epoch 21, Validation Loss: 0.86
Epoch 22, Validation Loss: 0.81
Epoch 23, Validation Loss: 0.71
Epoch 24, Validation Loss: 0.94
Epoch 25, Validation Loss: 0.62
Epoch 26, Validation Loss: 0.57
Epoch 27, Validation Loss: 0.61
Epoch 28, Validation Loss: 0.56
Epoch 29, Validation Loss: 0.67
Epoch 30, Validation Loss: 0.55
Epoch 31, Valid

In [22]:
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"][:100]):
    # data point as tensor
    datapoints = {"b": torch.unsqueeze(b, 0).to("cuda"), 
                  "name": "test"}
    # infer
    components.eval()
    tick = time.time()
    with torch.no_grad():
        for comp in components:
            datapoints.update(comp(datapoints))
    tock = time.time()
    # assign params
    model.set_param_val({"b":b.cpu().numpy()})
    # assign vars
    x = datapoints["x_rnd"]
    for i in range(num_var):
        model.vars["x"][i].value = x[0,i].item()
    # get solutions
    xval, objval = model.get_val()    
    params.append(list(b.cpu().numpy()))
    sols.append(list(list(xval.values())[0].values()))
    objvals.append(objval)
    conviols.append(sum(model.cal_violation()))
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
df.to_csv("result/nc_lt_50-50.csv")

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [00:01<00:00, 69.68it/s]


          Obj Val  Constraints Viol  Elapsed Time
count  100.000000             100.0    100.000000
mean     0.423818               0.0      0.003323
std      0.069913               0.0      0.001062
min      0.257043               0.0      0.001993
25%      0.375288               0.0      0.002512
50%      0.409501               0.0      0.003008
75%      0.475931               0.0      0.004000
max      0.625261               0.0      0.006062
Number of infeasible solution: 0


## Parametric Learning Then Rounding

In [23]:
# random seed
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed(42)

In [24]:
# hyperparameters
penalty_weight = 100  # weight of constraint violation penealty
hlayers_sol = 5       # number of hidden layers for solution mapping
hsize = 128           # width of hidden layers for solution mapping
lr = 1e-3             # learning rate

In [25]:
# set problem
import neuromancer as nm
from src.problem import nmQuadratic
from src.func.layer import netFC
# build neural architecture for the solution map
func = nm.modules.blocks.MLP(insize=num_ineq, outsize=num_var, bias=True,
                             linear_map=nm.slim.maps["linear"],
                             nonlin=nn.ReLU, hsizes=[hsize]*hlayers_sol)
smap = nm.system.Node(func, ["b"], ["x"], name="smap")
# build neuromancer problem for rounding
components = nn.ModuleList([smap]).to("cuda")
loss_fn = nmQuadratic(["b", "x"], num_var, num_ineq, penalty_weight)

In [26]:
from src.problem.neuromancer.trainer import trainer
# training
epochs = 200                    # number of training epochs
warmup = 20                     # number of epochs to wait before enacting early stopping policy
patience = 20                   # number of epochs with no improvement in eval metric to allow before early stopping
optimizer = torch.optim.AdamW(components.parameters(), lr=lr)
# create a trainer for the problem
my_trainer = trainer(components, loss_fn, optimizer, epochs, patience, warmup, device="cuda")
# training for the rounding problem
my_trainer.train(loader_train, loader_dev)

Epoch 0, Validation Loss: 1248.58
Epoch 1, Validation Loss: -7.98
Epoch 2, Validation Loss: -11.57
Epoch 3, Validation Loss: -12.33
Epoch 4, Validation Loss: -12.14
Epoch 5, Validation Loss: -12.47
Epoch 6, Validation Loss: -12.71
Epoch 7, Validation Loss: -12.66
Epoch 8, Validation Loss: -12.58
Epoch 9, Validation Loss: -12.68
Epoch 10, Validation Loss: -12.67
Epoch 11, Validation Loss: -12.74
Epoch 12, Validation Loss: -12.57
Epoch 13, Validation Loss: -12.90
Epoch 14, Validation Loss: -12.74
Epoch 15, Validation Loss: -12.56
Epoch 16, Validation Loss: -12.80
Epoch 17, Validation Loss: -12.96
Epoch 18, Validation Loss: -12.35
Epoch 19, Validation Loss: -12.84
Epoch 20, Validation Loss: -12.71
Epoch 21, Validation Loss: -12.95
Epoch 22, Validation Loss: -12.91
Epoch 23, Validation Loss: -12.94
Epoch 24, Validation Loss: -13.25
Epoch 25, Validation Loss: -13.28
Epoch 26, Validation Loss: -13.11
Epoch 27, Validation Loss: -13.28
Epoch 28, Validation Loss: -13.32
Epoch 29, Validation Los

In [27]:
from src.heuristic import naive_round
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"][:100]):
    # data point as tensor
    datapoints = {"b": torch.unsqueeze(b, 0).to("cuda"), 
                  "name": "test"}
    # infer
    components.eval()
    tick = time.time()
    with torch.no_grad():
        for comp in components:
            datapoints.update(comp(datapoints))
    tock = time.time()
    # assign params
    model.set_param_val({"b":b.cpu().numpy()})
    # assign vars
    x = datapoints["x"]
    for i in range(num_var):
        model.vars["x"][i].value = x[0,i].item()
    # get solutions
    xval_rel, _ = model.get_val()
    xval, objval = naive_round(xval_rel, model)
    params.append(list(b.cpu().numpy()))
    sols.append(list(list(xval.values())[0].values()))
    objvals.append(objval)
    conviols.append(sum(model.cal_violation()))
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
df.to_csv("result/nc_pr_50-50.csv")

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [00:01<00:00, 74.50it/s]


          Obj Val  Constraints Viol  Elapsed Time
count  100.000000        100.000000    100.000000
mean    16.625967          0.061082      0.000721
std      1.096638          0.104191      0.000472
min     13.756893          0.000000      0.000000
25%     15.901262          0.000000      0.000000
50%     16.784503          0.000000      0.001000
75%     17.348345          0.082220      0.001001
max     19.499876          0.498455      0.001576
Number of infeasible solution: 44


### STE Rounding

In [7]:
# random seed
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed(42)

In [8]:
# hyperparameters
penalty_weight = 100  # weight of constraint violation penealty
hlayers_sol = 5       # number of hidden layers for solution mapping
hsize = 16            # width of hidden layers for solution mapping
lr = 1e-3             # learning rate

In [9]:
# set problem
import neuromancer as nm
from src.problem import nmQuadratic
from src.func.layer import netFC
from src.func import roundSTEModel
# build neural architecture for the solution map
func = nm.modules.blocks.MLP(insize=num_ineq, outsize=num_var, bias=True,
                             linear_map=nm.slim.maps["linear"],
                             nonlin=nn.ReLU, hsizes=[hsize]*hlayers_sol)
smap = nm.system.Node(func, ["b"], ["x"], name="smap")
# define rounding model
rnd = roundSTEModel(param_keys=["b"], var_keys=["x"],  output_keys=["x_rnd"], int_ind=model.int_ind, name="round")
# build neuromancer problem for rounding
components = nn.ModuleList([smap, rnd]).to("cuda")
loss_fn = nmQuadratic(["b", "x_rnd"], num_var, num_ineq, penalty_weight)

In [10]:
from src.problem.neuromancer.trainer import trainer
# training
epochs = 200                    # number of training epochs
warmup = 20                     # number of epochs to wait before enacting early stopping policy
patience = 20                   # number of epochs with no improvement in eval metric to allow before early stopping
optimizer = torch.optim.AdamW(components.parameters(), lr=lr)
# create a trainer for the problem
my_trainer = trainer(components, loss_fn, optimizer, epochs, patience, warmup, device="cuda")
# training for the rounding problem
my_trainer.train(loader_train, loader_dev)

Epoch 0, Validation Loss: 1241.19
Epoch 1, Validation Loss: 15.54
Epoch 2, Validation Loss: -0.70
Epoch 3, Validation Loss: -3.47
Epoch 4, Validation Loss: -6.03
Epoch 5, Validation Loss: -8.40
Epoch 6, Validation Loss: -10.00
Epoch 7, Validation Loss: -10.46
Epoch 8, Validation Loss: -10.59
Epoch 9, Validation Loss: -11.02
Epoch 10, Validation Loss: -11.19
Epoch 11, Validation Loss: -10.88
Epoch 12, Validation Loss: -11.29
Epoch 13, Validation Loss: -11.07
Epoch 14, Validation Loss: -10.93
Epoch 15, Validation Loss: -11.12
Epoch 16, Validation Loss: -11.04
Epoch 17, Validation Loss: -11.37
Epoch 18, Validation Loss: -11.15
Epoch 19, Validation Loss: -11.41
Epoch 20, Validation Loss: -11.20
Epoch 21, Validation Loss: -11.18
Epoch 22, Validation Loss: -11.16
Epoch 23, Validation Loss: -11.30
Epoch 24, Validation Loss: -10.98
Epoch 25, Validation Loss: -11.23
Epoch 26, Validation Loss: -11.13
Epoch 27, Validation Loss: -11.33
Epoch 28, Validation Loss: -11.43
Epoch 29, Validation Loss: -

In [11]:
from src.heuristic import naive_round
params, sols, objvals, conviols, elapseds = [], [], [], [], []
for b in tqdm(data_test.datadict["b"][:100]):
    # data point as tensor
    datapoints = {"b": torch.unsqueeze(b, 0).to("cuda"), 
                  "name": "test"}
    # infer
    components.eval()
    tick = time.time()
    with torch.no_grad():
        for comp in components:
            datapoints.update(comp(datapoints))
    tock = time.time()
    # assign params
    model.set_param_val({"b":b.cpu().numpy()})
    # assign vars
    x = datapoints["x"]
    for i in range(num_var):
        model.vars["x"][i].value = x[0,i].item()
    # get solutions
    xval_rel, _ = model.get_val()
    xval, objval = naive_round(xval_rel, model)
    params.append(list(b.cpu().numpy()))
    sols.append(list(list(xval.values())[0].values()))
    objvals.append(objval)
    conviols.append(sum(model.cal_violation()))
    elapseds.append(tock - tick)
df = pd.DataFrame({"Param":params, "Sol":sols, "Obj Val": objvals, "Constraints Viol": conviols, "Elapsed Time": elapseds})
time.sleep(1)
print(df.describe())
print("Number of infeasible solution: {}".format(np.sum(df["Constraints Viol"] > 0)))
df.to_csv("result/nc_st_50-50.csv")

100%|████████████████████████████████████████████████████████████████████████████████| 100/100 [00:01<00:00, 69.07it/s]


          Obj Val  Constraints Viol  Elapsed Time
count  100.000000             100.0    100.000000
mean    15.958720               0.0      0.001685
std      1.199616               0.0      0.000551
min     12.958658               0.0      0.000999
25%     15.003178               0.0      0.001058
50%     15.961331               0.0      0.001759
75%     16.722273               0.0      0.002081
max     18.946539               0.0      0.002928
Number of infeasible solution: 0
